# Part 1

## Import libraries, modules and functions

In [1]:
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
import requests 

## Scrape data from HTML tables into a DataFrame using read_html

In [2]:
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'

In [3]:
dataframe_list = pd.read_html(url, flavor='bs4')

In [4]:
df = dataframe_list[0]
df

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
..          ...               ...   
175         M5Z      Not assigned   
176         M6Z      Not assigned   
177         M7Z      Not assigned   
178         M8Z         Etobicoke   
179         M9Z      Not assigned   

                                         Neighbourhood  
0                                         Not assigned  
1                                         Not assigned  
2                                            Parkwoods  
3                                     Victoria Village  
4                            Regent Park, Harbourfront  
..                                                 ...  
175                                       Not assigned  
176                                       Not assigned  
177                                       Not assigned  
178  Mimico NW, The Queensway West, South of Bloor,...  
179                                       Not assigned  

[180 rows x 3 columns]

#### Drop rows with 'Not assigned' Borough

In [5]:
df.drop(df.loc[df['Borough']=='Not assigned'].index, inplace=True)
df = df.reset_index(drop=True)
df.head(10)

Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
5         M9A         Etobicoke      Islington Avenue, Humber Valley Village
6         M1B       Scarborough                               Malvern, Rouge
7         M3B        North York                                    Don Mills
8         M4B         East York              Parkview Hill, Woodbine Gardens
9         M5B  Downtown Toronto                     Garden District, Ryerson

In [6]:
#### Find rows with 'Not assigned' Neighbourhouds

In [7]:
df.loc[df['Neighbourhood'] == 'Not assigned']

Empty DataFrame
Columns: [Postal Code, Borough, Neighbourhood]
Index: []

In [8]:
df.shape

(103, 3)

# Part 2

## Install and import libraries, modules and functions

In [9]:
!pip install geocoder

In [10]:
import geocoder # import geocoder

## Get latitude and longitude for each neighbourhoud

In [11]:
!pip install pgeocode
import pgeocode
pgeocode.Nominatim('ca')
geolocator = pgeocode.Nominatim('ca')
postal_codes = df['Postal Code'].tolist()
latitudes = []
longitudes = []
for i, postal_code in enumerate(postal_codes):
    # initialize your variable to None
    #print(f'--Getting Postal Code: {postal_code}')
    g = geolocator.query_postal_code(postal_code)
    
    if not g.empty:
        #print(f'Postal Code {postal_code} has been retrieved. {len(postal_codes) - (i + 1)} codes left')
        latitudes.append(g.latitude)
        longitudes.append(g.longitude)

In [12]:
df['Latitude'] = latitudes
df['Longitude'] = longitudes
df

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood  Latitude  Longitude  
0                                            Parkwoods   43.7545   -79.3300  
1                                     Victoria Village   43.7276   -79.3148  
2                            Regent Park, Harbourfront   43.6555   -79.3626  
3                     Lawrence Manor, Lawrence Heights   43.7223   -79.4504  
4          Queen's Park, Ontario Provincial Government   43.6641   -79.3889  
..                                                 ...       ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North   43.6518   -79.5076  
99                                Church and Wellesley   43.6656   -79.3830  
100  Business reply mail Processing Centre, South C...   43.7804   -79.2505  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...   43.6325   -79.4939  
102  Mimico NW, The Queensway West, South of Bloor,...   43.6256   -79.5231  

[103 rows x 5 columns]

# Part 3

## Install and import libraries, modules and functions 

In [13]:
import json
from geopy.geocoders import Nominatim
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium

Solving environment: done

# All requested packages already installed.



## Use geopy library to get the latitude and longitude values of Toronto

In [14]:
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


### Drop nan values

In [15]:
df = df.dropna()
df

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood  Latitude  Longitude  
0                                            Parkwoods   43.7545   -79.3300  
1                                     Victoria Village   43.7276   -79.3148  
2                            Regent Park, Harbourfront   43.6555   -79.3626  
3                     Lawrence Manor, Lawrence Heights   43.7223   -79.4504  
4          Queen's Park, Ontario Provincial Government   43.6641   -79.3889  
..                                                 ...       ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North   43.6518   -79.5076  
99                                Church and Wellesley   43.6656   -79.3830  
100  Business reply mail Processing Centre, South C...   43.7804   -79.2505  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...   43.6325   -79.4939  
102  Mimico NW, The Queensway West, South of Bloor,...   43.6256   -79.5231  

[102 rows x 5 columns]

## Create map of Toronto using latitude and longitude values 

In [16]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighbourhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Define Foursquare Credentials and Version 

In [17]:
CLIENT_ID = 'G0GPEATC5GTGWNIL3TDEHXZ0FEPB4VE1TXSDYZRZUFF3QFMD' # your Foursquare ID
CLIENT_SECRET = '34DS1POLVF0VYZ2HT53EB1OMOGVO5ZNKN5SZP34PTXY3GQVS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: G0GPEATC5GTGWNIL3TDEHXZ0FEPB4VE1TXSDYZRZUFF3QFMD
CLIENT_SECRET:34DS1POLVF0VYZ2HT53EB1OMOGVO5ZNKN5SZP34PTXY3GQVS


#### Let's explore the first neighborhood in our dataframe 

In [18]:
df.loc[0, 'Neighbourhood']

'Parkwoods'

#### Get the neighborhood's latitude and longitude values.

In [19]:
neighbourhood_latitude = df.loc[0, 'Latitude'] # neighborhood latitude value
neighbourhood_longitude = df.loc[0, 'Longitude'] # neighborhood longitude value

neighbourhood_name = df.loc[0, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighbourhood_name, 
                                                               neighbourhood_latitude, 
                                                               neighbourhood_longitude))

Latitude and longitude values of Parkwoods are 43.7545, -79.33.


#### Now, let's get the top 100 venues that are in Parkwoods within a radius of 500 meters.

In [20]:
radius = 500
url ='https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighbourhood_latitude, 
    neighbourhood_longitude, 
    radius, 
    LIMIT)


In [21]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '6043bde50694d72733efe14d'},
 'response': {'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 4,
  'suggestedBounds': {'ne': {'lat': 43.7590000045, 'lng': -79.32378161085641},
   'sw': {'lat': 43.7499999955, 'lng': -79.33621838914358}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.751976046055574,
          'lng': -79.33214044722958}],
        'distance': 329,
        'cc': 'CA',
       

In [22]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [23]:
import pandas

print(pandas.__version__)

1.2.3


In [24]:
!pip install --upgrade pandas

In [25]:
!conda install -c conda-forge geopy --yes

Solving environment: done

# All requested packages already installed.



In [26]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/ipykernel/__main__.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  app.launch_new_instance()


name                  categories        lat  \
0                    Brookbanks Park                        Park  43.751976   
1                Towns On The Ravine                       Hotel  43.754754   
2                      Variety Store           Food & Drink Shop  43.751974   
3  Corrosion Service Company Limited  Construction & Landscaping  43.752432   

         lng  
0 -79.332140  
1 -79.332552  
2 -79.333114  
3 -79.334661

In [27]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

4 venues were returned by Foursquare.


## Explore Neighborhoods in Toronto

In [28]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [29]:
df = getNearbyVenues(names=df['Neighbourhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [30]:
df.shape
df

Neighbourhood  \
0                                             Parkwoods   
1                                             Parkwoods   
2                                             Parkwoods   
3                                             Parkwoods   
4                                      Victoria Village   
...                                                 ...   
2141  Mimico NW, The Queensway West, South of Bloor,...   
2142  Mimico NW, The Queensway West, South of Bloor,...   
2143  Mimico NW, The Queensway West, South of Bloor,...   
2144  Mimico NW, The Queensway West, South of Bloor,...   
2145  Mimico NW, The Queensway West, South of Bloor,...   

      Neighbourhood Latitude  Neighbourhood Longitude  \
0                    43.7545                 -79.3300   
1                    43.7545                 -79.3300   
2                    43.7545                 -79.3300   
3                    43.7545                 -79.3300   
4                    43.7276                 -79.3148   
...                      ...                      ...   
2141                 43.6256                 -79.5231   
2142                 43.6256                 -79.5231   
2143                 43.6256                 -79.5231   
2144                 43.6256                 -79.5231   
2145                 43.6256                 -79.5231   

                                  Venue  Venue Latitude  Venue Longitude  \
0                       Brookbanks Park       43.751976       -79.332140   
1                   Towns On The Ravine       43.754754       -79.332552   
2                         Variety Store       43.751974       -79.333114   
3     Corrosion Service Company Limited       43.752432       -79.334661   
4                Victoria Village Arena       43.723481       -79.315635   
...                                 ...             ...              ...   
2141               Kingsway Boxing Club       43.627254       -79.526684   
2142                             Solmaz       43.626773       -79.527259   
2143                    Mandarin Buffet       43.621352       -79.523015   
2144                   Buon Giorno Cafe       43.622801       -79.519322   
2145         Royal Canadian Legion #210       43.628855       -79.518903   

                  Venue Category  
0                           Park  
1                          Hotel  
2              Food & Drink Shop  
3     Construction & Landscaping  
4                   Hockey Arena  
...                          ...  
2141                         Gym  
2142           Food & Drink Shop  
2143                      Buffet  
2144          Italian Restaurant  
2145                 Social Club  

[2146 rows x 7 columns]

In [31]:
df.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                             
Agincourt                                                             4   
Alderwood, Long Branch                                                7   
Bathurst Manor, Wilson Heights, Downsview North                       7   
Bayview Village                                                       5   
Bedford Park, Lawrence Manor East                                    26   
...                                                                 ...   
Willowdale, Willowdale West                                           4   
Woburn                                                                1   
Woodbine Heights                                                      4   
York Mills West                                                       2   
York Mills, Silver Hills                                              1   

                                                 Neighbourhood Longitude  \
Neighbourhood                                                              
Agincourt                                                              4   
Alderwood, Long Branch                                                 7   
Bathurst Manor, Wilson Heights, Downsview North                        7   
Bayview Village                                                        5   
Bedford Park, Lawrence Manor East                                     26   
...                                                                  ...   
Willowdale, Willowdale West                                            4   
Woburn                                                                 1   
Woodbine Heights                                                       4   
York Mills West                                                        2   
York Mills, Silver Hills                                               1   

                                                 Venue  Venue Latitude  \
Neighbourhood                                                            
Agincourt                                            4               4   
Alderwood, Long Branch                               7               7   
Bathurst Manor, Wilson Heights, Downsview North      7               7   
Bayview Village                                      5               5   
Bedford Park, Lawrence Manor East                   26              26   
...                                                ...             ...   
Willowdale, Willowdale West                          4               4   
Woburn                                               1               1   
Woodbine Heights                                     4               4   
York Mills West                                      2               2   
York Mills, Silver Hills                             1               1   

                                                 Venue Longitude  \
Neighbourhood                                                      
Agincourt                                                      4   
Alderwood, Long Branch                                         7   
Bathurst Manor, Wilson Heights, Downsview North                7   
Bayview Village                                                5   
Bedford Park, Lawrence Manor East                             26   
...                                                          ...   
Willowdale, Willowdale West                                    4   
Woburn                                                         1   
Woodbine Heights                                               4   
York Mills West                                                2   
York Mills, Silver Hills                                       1   

                                                 Venue Category  
Neighbourhood                                                    
Agincourt                                                     4  
Alderwood, Long Branch                

In [32]:
print('There are {} uniques categories.'.format(len(df['Venue Category'].unique())))

There are 257 uniques categories.


##  Analyze Each Neighborhood

In [33]:
# one hot encoding
df_onehot = pd.get_dummies(df[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
df_onehot['Neighbourhood'] = df['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [df_onehot.columns[-1]] + list(df_onehot.columns[:-1])
df_onehot = df_onehot[fixed_columns]

df_onehot.head()

Neighbourhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2         Parkwoods                  0                  0        0   
3         Parkwoods                  0                  0        0   
4  Victoria Village                  0                  0        0   

   American Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                    0            0           0                    0   
1                    0            0           0                    0   
2                    0            0           0                    0   
3                    0            0           0                    0   
4                    0            0           0                    0   

   Asian Restaurant  Athletics & Sports  ...  Video Game Store  Video Store  \
0                 0                   0  ...                 0            0   
1                 0                   0  ...                 0            0   
2                 0                   0  ...                 0            0   
3                 0                   0  ...                 0            0   
4                 0                   0  ...                 0            0   

   Vietnamese Restaurant  Warehouse Store  Whisky Bar  Wine Bar  Wine Shop  \
0                      0                0           0         0          0   
1                      0                0           0         0          0   
2                      0                0           0         0          0   
3                      0                0           0         0          0   
4                      0                0           0         0          0   

   Wings Joint  Women's Store  Yoga Studio  
0            0              0            0  
1            0              0            0  
2            0              0            0  
3            0              0            0  
4            0              0            0  

[5 rows x 258 columns]

In [34]:
df_onehot.shape

(2146, 258)

In [35]:
df_grouped = df_onehot.groupby('Neighbourhood').mean().reset_index()
df_grouped

Neighbourhood  Accessories Store  \
0                                         Agincourt                0.0   
1                            Alderwood, Long Branch                0.0   
2   Bathurst Manor, Wilson Heights, Downsview North                0.0   
3                                   Bayview Village                0.0   
4                 Bedford Park, Lawrence Manor East                0.0   
..                                              ...                ...   
91                      Willowdale, Willowdale West                0.0   
92                                           Woburn                0.0   
93                                 Woodbine Heights                0.0   
94                                  York Mills West                0.0   
95                         York Mills, Silver Hills                0.0   

    Afghan Restaurant  Airport  American Restaurant  Art Gallery  Art Museum  \
0                 0.0      0.0             0.000000          0.0         0.0   
1                 0.0      0.0             0.000000          0.0         0.0   
2                 0.0      0.0             0.000000          0.0         0.0   
3                 0.0      0.0             0.000000          0.0         0.0   
4                 0.0      0.0             0.038462          0.0         0.0   
..                ...      ...                  ...          ...         ...   
91                0.0      0.0             0.000000          0.0         0.0   
92                0.0      0.0             0.000000          0.0         0.0   
93                0.0      0.0             0.000000          0.0         0.0   
94                0.0      0.0             0.000000          0.0         0.0   
95                0.0      0.0             0.000000          0.0         0.0   

    Arts & Crafts Store  Asian Restaurant  Athletics & Sports  ...  \
0                   0.0               0.0                 0.0  ...   
1                   0.0               0.0                 0.0  ...   
2                   0.0               0.0                 0.0  ...   
3                   0.0               0.0                 0.0  ...   
4                   0.0               0.0                 0.0  ...   
..                  ...               ...                 ...  ...   
91                  0.0               0.0                 0.0  ...   
92                  0.0               0.0                 0.0  ...   
93                  0.0               0.0                 0.0  ...   
94                  0.0               0.0                 0.0  ...   
95                  0.0               0.0                 0.0  ...   

    Video Game Store  Video Store  Vietnamese Restaurant  Warehouse Store  \
0                0.0         0.00                    0.0              0.0   
1                0.0         0.00                    0.0              0.0   
2                0.0         0.00                    0.0              0.0   
3                0.0         0.00                    0.0              0.0   
4                0.0         0.00                    0.0              0.0   
..               ...          ...                    ...              ...   
91               0.0         0.00                    0.0              0.0   
92               0.0         0.00                    0.0              0.0   
93               0.0         0.25                    0.0              0.0   
94               0.0         0.00                    0.0              0.0   
95               0.0         0.00                    0.0              0.0   

    Whisky Bar  Wine Bar  Wine Shop  Wings Joint  Women's Store  Yoga Studio  
0          0.0       0.0        0.0          0.0       0.000000          0.0  
1          0.0       0.0        0.0          0.0       0.000000          0.0  
2          0.0       0.0        0.0          0.0       0.000000          0.0  
3          0.0       0.0        0.0          0.0       0.000000          0.0  
4          0.0       0.0   

In [36]:
df_grouped.shape

(96, 258)

In [37]:
num_top_venues = 5

for hood in df_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = df_grouped[df_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                       venue  freq
0  Latin American Restaurant  0.25
1             Breakfast Spot  0.25
2            Badminton Court  0.25
3               Skating Rink  0.25
4              Moving Target  0.00


----Alderwood, Long Branch----
               venue  freq
0        Pizza Place  0.14
1        Coffee Shop  0.14
2  Convenience Store  0.14
3           Pharmacy  0.14
4                Pub  0.14


----Bathurst Manor, Wilson Heights, Downsview North----
                       venue  freq
0                Pizza Place  0.14
1  Middle Eastern Restaurant  0.14
2              Deli / Bodega  0.14
3        Fried Chicken Joint  0.14
4              Grocery Store  0.14


----Bayview Village----
         venue  freq
0        Trail   0.2
1  Flower Shop   0.2
2         Park   0.2
3  Gas Station   0.2
4      Dog Run   0.2


----Bedford Park, Lawrence Manor East----
                venue  freq
0         Coffee Shop  0.08
1  Italian Restaurant  0.08
2      Sandwich Place  0.08
3

----Parkview Hill, Woodbine Gardens----
          venue  freq
0   Pizza Place   0.2
1          Café   0.1
2     Gastropub   0.1
3  Intersection   0.1
4      Pharmacy   0.1


----Parkwoods----
                        venue  freq
0                       Hotel  0.25
1                        Park  0.25
2           Food & Drink Shop  0.25
3  Construction & Landscaping  0.25
4                Neighborhood  0.00


----Queen's Park, Ontario Provincial Government----
                venue  freq
0    Sushi Restaurant  0.08
1   College Cafeteria  0.08
2  Italian Restaurant  0.04
3     College Theater  0.04
4                 Gym  0.04


----Regent Park, Harbourfront----
               venue  freq
0        Coffee Shop  0.21
1     Breakfast Spot  0.08
2        Yoga Studio  0.04
3  Health Food Store  0.04
4                Spa  0.04


----Richmond, Adelaide, King----
         venue  freq
0  Coffee Shop  0.07
1         Café  0.07
2   Restaurant  0.05
3          Gym  0.04
4        Hotel  0.03


----Rosed

In [38]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [39]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = df_grouped['Neighbourhood']

for ind in np.arange(df_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(df_grouped.iloc[ind, :], num_top_venues)

neighbourhoods_venues_sorted.head()

Neighbourhood      1st Most Common Venue  \
0                                        Agincourt  Latin American Restaurant   
1                           Alderwood, Long Branch                Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                Pizza Place   
3                                  Bayview Village                      Trail   
4                Bedford Park, Lawrence Manor East                Coffee Shop   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0             Breakfast Spot       Badminton Court          Skating Rink   
1                Coffee Shop     Convenience Store              Pharmacy   
2  Middle Eastern Restaurant         Deli / Bodega   Fried Chicken Joint   
3                Flower Shop                  Park           Gas Station   
4         Italian Restaurant        Sandwich Place           Pizza Place   

  5th Most Common Venue     6th Most Common Venue 7th Most Common Venue  \
0         Moving Target              Neighborhood           Music Venue   
1                   Pub                       Gym        Sandwich Place   
2         Grocery Store  Mediterranean Restaurant           Coffee Shop   
3               Dog Run         Accessories Store   Moroccan Restaurant   
4      Toy / Game Store                      Café               Butcher   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0           Music Store                Museum          Movie Theater  
1     Accessories Store                Museum           Neighborhood  
2     Accessories Store         Moving Target            Music Store  
3           Music Store                Museum          Moving Target  
4        Breakfast Spot  Fast Food Restaurant       Sushi Restaurant

In [40]:
# set number of clusters
kclusters = 5

df_grouped_clustering = df_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(df_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 0, 0, 2, 2, 2, 2, 2, 2, 2], dtype=int32)

In [41]:
# add clustering labels
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

df_merged = df

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
df_merged = df_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

df_merged.head() # check the last columns!

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0         Parkwoods                 43.7545                 -79.3300   
1         Parkwoods                 43.7545                 -79.3300   
2         Parkwoods                 43.7545                 -79.3300   
3         Parkwoods                 43.7545                 -79.3300   
4  Victoria Village                 43.7276                 -79.3148   

                               Venue  Venue Latitude  Venue Longitude  \
0                    Brookbanks Park       43.751976       -79.332140   
1                Towns On The Ravine       43.754754       -79.332552   
2                      Variety Store       43.751974       -79.333114   
3  Corrosion Service Company Limited       43.752432       -79.334661   
4             Victoria Village Arena       43.723481       -79.315635   

               Venue Category  Cluster Labels 1st Most Common Venue  \
0                        Park               2                 Hotel   
1                       Hotel               2                 Hotel   
2           Food & Drink Shop               2                 Hotel   
3  Construction & Landscaping               2                 Hotel   
4                Hockey Arena               2           Pizza Place   

  2nd Most Common Venue 3rd Most Common Venue       4th Most Common Venue  \
0                  Park     Food & Drink Shop  Construction & Landscaping   
1                  Park     Food & Drink Shop  Construction & Landscaping   
2                  Park     Food & Drink Shop  Construction & Landscaping   
3                  Park     Food & Drink Shop  Construction & Landscaping   
4     French Restaurant          Intersection                Hockey Arena   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0           Neighborhood           Music Venue           Music Store   
1           Neighborhood           Music Venue           Music Store   
2           Neighborhood           Music Venue           Music Store   
3           Neighborhood           Music Venue           Music Store   
4  Portuguese Restaurant           Coffee Shop                  Park   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                Museum         Moving Target    Moroccan Restaurant  
1                Museum         Moving Target    Moroccan Restaurant  
2                Museum         Moving Target    Moroccan Restaurant  
3                Museum         Moving Target    Moroccan Restaurant  
4     Accessories Store         Movie Theater            Music Venue

In [44]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df_merged['Neighbourhood Latitude'], df_merged['Neighbourhood Longitude'], df_merged['Neighbourhood'], df_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [47]:
df_merged.loc[df_merged['Cluster Labels'] == 0, df.columns[[1] + list(range(5, df.shape[1]))]]

Neighbourhood Latitude  Venue Longitude              Venue Category
252                  43.7081       -79.443126                      Bakery
253                  43.7081       -79.453331   Latin American Restaurant
254                  43.7081       -79.443930         Japanese Restaurant
255                  43.7081       -79.452979               Grocery Store
256                  43.7081       -79.453421              Ice Cream Shop
257                  43.7081       -79.453488                 Pizza Place
258                  43.7081       -79.452238        Fast Food Restaurant
259                  43.7081       -79.453231                 Gas Station
260                  43.7081       -79.453121    Mediterranean Restaurant
261                  43.7081       -79.443141                 Pizza Place
262                  43.7081       -79.442658                 Pizza Place
263                  43.6505       -79.548694              Sandwich Place
264                  43.6505       -79.548726                 Pizza Place
265                  43.6505       -79.549000                 Pizza Place
266                  43.6505       -79.548866          Chinese Restaurant
267                  43.6505       -79.549124                    Tea Room
268                  43.6505       -79.545850  Construction & Landscaping
269                  43.6505       -79.545660                 Coffee Shop
623                  43.7535       -79.451690    Mediterranean Restaurant
624                  43.7535       -79.442438               Deli / Bodega
625                  43.7535       -79.443507   Middle Eastern Restaurant
626                  43.7535       -79.443250                 Coffee Shop
627                  43.7535       -79.442740         Fried Chicken Joint
628                  43.7535       -79.450926                 Pizza Place
629                  43.7535       -79.441669               Grocery Store
838                  43.7694       -79.489318              Massage Studio
839                  43.7694       -79.492741   Middle Eastern Restaurant
840                  43.7694       -79.492938                 Pizza Place
841                  43.7694       -79.493128              Sandwich Place
842                  43.7694       -79.491172               Metro Station
843                  43.7694       -79.492884                  Sports Bar
1237                 43.7247       -79.229640                      Bistro
1238                 43.7247       -79.235625              Ice Cream Shop
1239                 43.7247       -79.231471                 Coffee Shop
1240                 43.7247       -79.231626                    Pharmacy
1241                 43.7247       -79.230456              Sandwich Place
1242                 43.7247       -79.235452              Ice Cream Shop
1243                 43.7247       -79.235277                 Pizza Place
1244                 43.7247       -79.231379              Discount Store
1404                 43.6949       -79.531566          Chinese Restaurant
1405                 43.6949       -79.533398                 Coffee Shop
1406                 43.6949       -79.531471              Sandwich Place
1407                 43.6949       -79.533505                 Pizza Place
1408                 43.6949       -79.531010                 Supermarket
1409                 43.6949       -79.531570                 Pizza Place
1410                 43.6949       -79.531593              Discount Store
1411                 43.6949       -79.531702              Ice Cream Shop
1413                 43.7786       -79.444231                 Coffee Shop
1414                 43.7786       -79.443619                 Pizza Place
1415                 43.7786       -79.448705                        Park
1416                 43.7786       -79.447850                   Bookstore
1868                 43.6021       -79.545028                 Pizza Place
1869                 43.6021       -79.542924                         Gym
1870      

In [49]:
df_merged.loc[df_merged['Cluster Labels'] == 1, df.columns[[1] + list(range(5, df.shape[1]))]]

Neighbourhood Latitude  Venue Longitude  \
622                  43.8015       -79.352840   
773                  43.7464       -79.231609   
774                  43.7464       -79.230190   
1377                 43.7301       -79.394382   
1378                 43.7301       -79.388767   
1387                 43.7068       -79.521705   
1390                 43.7500       -79.399717   
1391                 43.7500       -79.401393   
1402                 43.6605       -79.463038   
1403                 43.6605       -79.464438   

                                Venue Category  
622                                       Park  
773                              Grocery Store  
774                                       Park  
1377                                      Park  
1378                        Photography Studio  
1387                                      Park  
1390                                      Park  
1391                         Convenience Store  
1402                                      Park  
1403  Residential Building (Apartment / Condo)

In [50]:
df_merged.loc[df_merged['Cluster Labels'] == 2, df.columns[[1] + list(range(5, df.shape[1]))]]

Neighbourhood Latitude  Venue Longitude              Venue Category
0                    43.7545       -79.332140                        Park
1                    43.7545       -79.332552                       Hotel
2                    43.7545       -79.333114           Food & Drink Shop
3                    43.7545       -79.334661  Construction & Landscaping
4                    43.7276       -79.315635                Hockey Arena
...                      ...              ...                         ...
2141                 43.6256       -79.526684                         Gym
2142                 43.6256       -79.527259           Food & Drink Shop
2143                 43.6256       -79.523015                      Buffet
2144                 43.6256       -79.519322          Italian Restaurant
2145                 43.6256       -79.518903                 Social Club

[2074 rows x 3 columns]

In [51]:
df_merged.loc[df_merged['Cluster Labels'] == 3, df.columns[[1] + list(range(5, df.shape[1]))]]

Neighbourhood Latitude  Venue Longitude Venue Category
1740                 43.6075       -79.506748      Gift Shop

In [52]:
df_merged.loc[df_merged['Cluster Labels'] == 4, df.columns[[1] + list(range(5, df.shape[1]))]]

Neighbourhood Latitude  Venue Longitude           Venue Category
138                  43.8113       -79.191331             Home Service
1379                 43.7113       -79.420702             Home Service
1380                 43.7113       -79.415810  Health & Beauty Service